# Fortgeschrittenes Beispiel
In diesem Abschnitt wollen wir uns mit einem komplexeren Beispiel beschäftigen, um weitere Methoden von `iminuit` kennzulernen.
Hierzu betrachten wir ein Zählexperiment, z.B. ein Teilchendetektor, bei dem ein Energiespektrum aufgenommen wird. Für jedes Energieintervall (Bin) wird die Anzahl der registrierten Ereignisse bestimmt. Hierbei können wir annehmen, dass die Verteilung der gemessenen Anzahl durch eine Poisson-Verteilung beschrieben wird. Dann entspricht der Fehler in jedem Bin gerade $\sqrt n$. 
Dieses Spektrum soll aus zwei gauß-förmigen Peaks über einem exponentiellen Untergrund bestehen und wird mit Hilfe eines Zufallszahlengenerator "erzeugt".

Nun wollen wir die Messdaten mit Hilfe von `iminuit` fitten. Hierzu müssen wir zunächste zwei Module des packages importieren und eine Funktion für die Entladekurve des Kondensators definieren:

In [1]:
# Diese Zelle nur auf JupyterHub des ZDV ausführen um `iminuit` zu installieren!
# import sys
# import subprocess
# subprocess.check_call([
#     sys.executable, 
#     '-m',
#     'pip',
#     'install',
#     '--proxy',
#     'http://webproxy.zdv.uni-mainz.de:3128',
#     'iminuit'
# ])

In [2]:
from iminuit import Minuit, cost
import matplotlib.pyplot as plt
import numpy as np

In [ ]:
rnd_bkd = np.random.exponential(39.7, 5000)
rnd_bkd += 40

peak1 = np.random.normal(53.3, 2.1, 5000)
peak2 = np.random.normal(60.5, 2.78, 12000)
data = np.concatenate([rnd_bkd, peak1, peak2])

entries, edges = np.histogram(data, bins=120, range=(40, 80))
center = edges[:-1] + np.diff(edges)/2

plt.errorbar(center, entries, np.sqrt(entries), ls='', marker='.')
plt.xlabel('Energy [keV]')
plt.ylabel('Number of counts per bin')

Zunächst wollen wir das Fitmodel in der Form

$$f(x) = A_1 \cdot \exp \bigg\{\frac{-(x - \mu_1)^2}{2 \cdot \sigma_1^2}\bigg\} + A_2 \cdot \exp \bigg\{\frac{-(x - \mu_2)^2}{2 \cdot \sigma_2^2}\bigg\} + A_3 \exp\{-x/\tau\}$$

definieren. Hier lohnt es sich, erst Funktionen für die einzelnen Komponenten zu definieren und dann das Gesamtmodel. Hierdurch lassen sich später die einzelnen Komponenten besser darstellen.

In [4]:
def peak(x, A, mu, sigma):
    return A*np.exp(-(x-mu)**2/(2*sigma**2))

def bkg(x, A, tau):
    return A*np.exp(-x/tau)

def fit_model(x, A_p1, A_p2, mu_p1, mu_p2, sigma_p1, sigma_p2, A_bkg, tau_bkg):
    return peak(x, A_p1, mu_p1, sigma_p1) + peak(x, A_p2, mu_p2, sigma_p2) + bkg(x, A_bkg, tau_bkg)

Nun wollen wir wieder die Kostenfunktion und die Minimierungsfunktion definieren. Startwerte können wir anhand unseres Plots ablesen, lediglich $\tau$ lässt sich auf diese Weise nicht gut bestimmen.

In [5]:
ls = cost.LeastSquares(center, entries, np.sqrt(entries), fit_model)

mi = Minuit(ls, 
            A_p1 = 400, 
            A_p2 = 700,
            mu_p1 = 54,
            mu_p2 = 60,
            sigma_p1 = 2,
            sigma_p2 = 2,
            A_bkg = 100,
            tau_bkg = 10, 
           )
mi.limits['tau_bkg'] = (0, None)

In [ ]:
plt.errorbar(center, entries, np.sqrt(entries), ls='', marker='.')
plt.xlabel('Energy [keV]')
plt.ylabel('Number of counts per bin')

x = np.arange(40, 80, 0.1)
plt.plot(x, fit_model(x, *mi.values), color='k', label='Initial guess')
plt.legend()

Unsere Startparameter sind bereits nicht schlecht, aber weichen noch stark von den Daten ab. Bei komplexeren Daten und Fitmodellen lohnt es sich, den Fit schrittweise durchzuführen. Bevor wir uns den beiden Peaks widmen, welche uns eigentlich interessieren, sollten wir versuchen, den Untergrund etwas besser zu beschreiben. Um den Untergrund besser fitten zu können, sollten wir erst den Fitbereich auf einen Energiebereich limitieren, in welchem der Untergrund dominiert. Dem Plot können wir entnehmen, dass dies für alle Werte unterhalb von 45 keV und oberhalb von 70 keV der Fall ist. Im Allgemeinen können wir Wertebereiche in Python mit Hilfe von „Masken“ selektieren. Eine Maske lässt sich wie folgt erstellen:

In [505]:
mask_outside_of_peaks = (center < 45) | (center >= 70)

Die Maske hat hierbei die Selbe länge wie unseren Daten…

In [ ]:
len(mask_outside_of_peaks), len(mask_outside_of_peaks)

… und beinhaltet Wahrheitswerte `True` und `False`, bzw. 1 und 0, mit welchen wir unsere Daten selektieren können:

In [ ]:
mask_outside_of_peaks, center[mask_outside_of_peaks]

Unsere Selektion können wir an unsere Kostenfunktion direkt übergeben.

In [508]:
ls.mask = (center < 45) | (center >= 70)

Nun können wir nochmal unsere Funktion und Messwerte für den ausgewählten Bereich plotten…

In [ ]:
plt.errorbar(center[ls.mask], entries[ls.mask], np.sqrt(entries[ls.mask]), ls='', marker='.', label='Not masked')
plt.errorbar(center[~ls.mask], entries[~ls.mask], np.sqrt(entries[~ls.mask]), ls='', marker='.', label='Masked')
plt.xlabel('Energy [keV]')
plt.ylabel('Number of counts per bin')

x = np.arange(40, 80, 0.1)
plt.plot(x, fit_model(x, *mi.values), color='k', label='Initial guess')
plt.legend()

Außerdem müssen wir noch alle Fitparameter, welche nicht zum Untergrund beitragen, als konstant festhalten

In [ ]:
mi.fixed[:] = True
mi.fixed[['tau_bkg', 'A_bkg']] = False
print (mi.fixed)

bevor wir die Minmierung starten und das Resultat darstellen.

In [ ]:
mi.migrad()
mi.hesse()

In [ ]:
plt.errorbar(center, entries, np.sqrt(entries), ls='', marker='.')
plt.xlabel('Energy [keV]')
plt.ylabel('Number of counts per bin')

x = np.arange(40, 80, 0.1)
plt.plot(x, fit_model(x, *mi.values), color='k', label='Initial guess')
plt.legend()


Das Resultat sieht bereits sehr gut aus. Nun können wir uns den eigentlichen Peaks widmen und starten im Folgenden mit dem kleineren der beiden. Zunächst sollten wir den maskierten Bereich entweder neu definieren oder komplett entfernen.

In [513]:
ls.mask = None

Außerdem können wir dem Plot entnehmen, dass durch den höheren Untergrund unsere Anfangsstartwerte nicht mehr ganz so gut passen. Diese können wir wie folgt aktualisieren:

In [514]:
mi.values['A_p1'] = 700
mi.values['sigma_p1'] = 3

Nun sollten wir alle Parameter wieder festhalten und nur die Parameter des ersten Peaks freigeben.

In [ ]:
mi.fixed[:] = True
mi.fixed[['A_p1', 'mu_p1', 'sigma_p1']] = False
mi.migrad()

Jetzt wiederholen wir das ganze für den zweiten Peak…

In [ ]:
mi.fixed[:] = True
mi.fixed[['A_p2', 'mu_p2', 'sigma_p2']] = False
mi.migrad()

Zum Schluss geben wir wieder alle Parameter frei und führen einen letzten Fit durch. 

In [ ]:
mi.fixed[:] = False
mi.migrad()

In [ ]:
plt.errorbar(center, entries, np.sqrt(entries), ls='', marker='.')
plt.xlabel('Energy [keV]')
plt.ylabel('Number of counts per bin')

x = np.arange(40, 80, 0.1)
plt.plot(x, fit_model(x, *mi.values), color='k', label='Best fit')
plt.plot(x, peak(x, *mi.values['A_p1', 'mu_p1', 'sigma_p1']), color='gray', ls='--', label='Peak 1')
plt.plot(x, peak(x, *mi.values['A_p2', 'mu_p2', 'sigma_p2']), color='gray', ls='-.', label='Peak 2')
plt.plot(x, bkg(x, *mi.values['A_bkg', 'tau_bkg']), color='gray', label='Background')
plt.legend()


Das Ergebnis sieht sehr gut aus. Alle Kacheln sind grün und die Daten scheinen durch die Funktion gut beschrieben zu werden. Natürlich können wir das gesamte Fitverfahren auch etwas kompakter in einer Zelle darstellen:

In [ ]:
ls = cost.LeastSquares(center, entries, np.sqrt(entries), fit_model)

mi = Minuit(ls, 
            A_p1 = 800, 
            A_p2 = 1400,
            mu_p1 = 54,
            mu_p2 = 60,
            sigma_p1 = 2,
            sigma_p2 = 2,
            A_bkg = 100,
            tau_bkg = 10, 
           )
mi.limits['tau_bkg'] = (0, None)
mi.fixed[:] = True
ls.mask = (center < 45) | (center >= 70)
mi.fixed[['tau_bkg', 'A_bkg']] = False
mi.migrad()
ls.mask = None
mi.values['A_p1'] = 700
mi.values['sigma_p1'] = 3
mi.fixed[:] = True
mi.fixed[['A_p1', 'mu_p1', 'sigma_p1']] = False
mi.migrad()
mi.fixed[:] = True
mi.fixed[['A_p2', 'mu_p2', 'sigma_p2']] = False
mi.migrad()
mi.fixed[:] = False
mi.migrad()

 # Wann fittet ein Fit?
Nach dem wir nun unser Model an unsere Daten angepasst haben, stellt sich die Frage: „Spiegelt unser Model unsere Daten gut wider?“.  Um diese Frage beantworten zu können, gibt es verschiedene Möglichkeiten, welche wir im Folgenden etwas näher betrachten wollen. 
## Fit Residual: 
Schauen wir uns zunächst noch einmal an, wie das Chi-Quadrat definiert ist:
$$ \chi^2 = \sum_i \frac{(y_i - \lambda_i)^2}{\Delta y_i^2} $$
Wir minimieren den Abstand zwischen einem Messwert und unserem Model und gewichten diesen mit den Unsicherheiten unserer Messwerte. Fitresiduen spiegeln genau dies wider. Sie sind definiert als 
$$ \frac{(y_i - \lambda_i)}{\Delta y_i} $$
Für unseren Fit sehen sie wie folgt aus.


In [ ]:
residuals = (entries - fit_model(center, *mi.values))/np.sqrt(entries)

plt.plot(center, residuals, ls='', marker='.')
plt.xlabel('Energy [keV]')
plt.ylabel('Residuals [$\sigma$]')

Als einzelner Plot sind sie noch nicht sehr informativ. Hilfreicher ist es bereits, wenn wir die Residuen zusammen mit unseren Daten und Fitmodel darstellen. 

In [ ]:
fig_fit = plt.figure(constrained_layout=True)
gs = fig_fit.add_gridspec(5, 5, hspace=0)


main_axis = fig_fit.add_subplot(gs[:4, :])
res_axis = fig_fit.add_subplot(gs[4:, :], sharex=main_axis)
fig_fit.tight_layout()


main_axis.errorbar(center, entries, np.sqrt(entries), ls='', marker='.', color='k')

main_axis.plot(x, peak(x, *mi.values['A_p1', 'mu_p1', 'sigma_p1']), color='gray', ls='--')
main_axis.plot(x, peak(x, *mi.values['A_p2', 'mu_p2', 'sigma_p2']), color='gray', ls='-.')
main_axis.plot(x, bkg(x, *mi.values['A_bkg', 'tau_bkg']), color='gray')

x = np.arange(40, 80, 0.1)
main_axis.plot(x, fit_model(x, *mi.values), color='purple', label='Best fit')
main_axis.legend()
main_axis.set_ylabel('Number of entries per bin')
main_axis.xaxis.set_tick_params(direction='inout')
main_axis.tick_params(axis='x', labelcolor=(0, 0, 0, 0))
main_axis.set_xlim(40, 80)

res_axis.set_xlabel('Energy [keV]')
res_axis.set_ylabel('Res [$\sigma$]')
res_axis.set_ylim(-3, 3)
res_axis.set_yticks([-2, 0,  2])
res_axis.fill_between((40, 80), -1, 1, alpha=0.3, color='purple')
res_axis.fill_between((40, 80), -2, 2, alpha=0.3, color='purple')
res_axis.axhline(0, color='purple')
res_axis.set_xlim(40, 80)
res_axis.plot(center, 
              residuals,
              color='k', marker='.', ls=''
             )
plt.tight_layout()

Sofern unser Fitmodel unsere Daten gut beschreibt, erwarten wir, dass die Residuen sich Gaußförmig zufällig um den Wert 0 herum verteilen. Dies folgt direkt aus der Annahme, dass sich die Unsicherheiten unserer Messwerte durch eine Gaußverteilung darstellen lassen. Dies können wir direkt überprüfen, sofern wir unsere Residuen in ein Histogramm eintragen. 

In [ ]:
plt.hist(residuals, bins=10, range=(-3, 3), histtype='step')
plt.xlabel('Residual [$\sigma$]')
plt.ylabel('#Entries per bin')
plt.show()

Bzw. den Anteil an Residuen berechnen, welcher innerhalb der 1 $\sigma$ Umgebung liegt.

In [ ]:
np.sum(np.abs(residuals) < 1)/len(residuals)

Zeigen unsere Residuen eine Struktur oder ein systematisches Verhalten, deutet dies auf einen ungenauen Fit oder ein falsches Fitmodel hin. Dies ist im Folgenden gezeigt. 

In [ ]:
pseudo_data = np.random.normal(0, 2, 5000)

fig_fit = plt.figure(constrained_layout=True)
gs = fig_fit.add_gridspec(5, 5, hspace=0)

main_axis = fig_fit.add_subplot(gs[:4, :])
res_axis = fig_fit.add_subplot(gs[4:, :], sharex=main_axis)
fig_fit.tight_layout()

entries1, edges1, _ = main_axis.hist(pseudo_data, bins=25, range=(-5,5), histtype='step', color='k')
center1 = edges1[:-1] + np.diff(edges1)/2

residuals1 = (entries1 - peak(center1, 400, 0.2, 2))/np.sqrt(entries1)

x = np.arange(-5, 5, 0.1)

main_axis.plot(x, peak(x, 400, 0.2, 2), color='purple')
main_axis.set_ylabel('Number of entries per bin')
main_axis.xaxis.set_tick_params(direction='inout')
main_axis.tick_params(axis='x', labelcolor=(0, 0, 0, 0))
main_axis.set_xlim(-5, 5)

res_axis.set_xlabel('Energy [keV]')
res_axis.set_ylabel('Res [$\sigma$]')
res_axis.set_ylim(-3, 3)
res_axis.set_yticks([-2, 0,  2])
res_axis.fill_between((-5, 5), -1, 1, alpha=0.3, color='purple')
res_axis.fill_between((-5, 5), -2, 2, alpha=0.3, color='purple')
res_axis.axhline(0, color='purple')
res_axis.set_xlim(-5, 5)
res_axis.plot(center1, 
              residuals1,
              color='k', marker='.', ls=''
             )
plt.tight_layout()

Zusätzlich zu den Fit-Residuen bietet das $\chi^2$ selbst einen Weg, um die „goodness-of-fit“ unseres Model bestimmen zu können ...

### $\chi^2$:

Wie gut fittet unsere obige Funktion unsere Messdaten? Sehr gut? Gut? Befriedigend? Oder doch eher schlecht?   Wäre es nicht gut, ein Maß für die Güte des Fits zu haben? Wie könnte ein solches Maß aussehen?

Sie haben das entscheidende Kriterium bereits kennengelernt: bei der Methode der kleinsten Quadrate geht es darum, das  $\chi^2$ zu minimieren. Gucken wir uns hierzu erst noch einmal an, wie sich das $\chi^2$ berechnet:

$$ \chi(\phi_1 ... \phi_N)^2 = \sum_{i = 1}^{N} \frac{ (y_i - \lambda(x_i; \phi))^2}{\Delta y_i^2}$$

Bei der Minimierung werden dabei Werte mit geringerer Unsicherheit bevorzugt, d.h. stärker gewichtet (s. Bild unten).

<figure class="image">
<img src="images/MaterialPythonkurs092018/LeastSquare.png"  alt="{{ Least Square Beispiel }}" width=80%>
</figure>

Damit man für einen gegebenen Datensatz nicht hunderte von verschiedenen Funktionen durchprobieren muss, gibt es für das $\chi^2$ eine allgemeine Faustregel, welche den berechneten $\chi^2$-Wert mit der Anzahl unserer Freiheitsgrade vergleicht. Die Anzahl an Freiheitsgrade ist gemeinhin gegeben als *Anzahl der Messwerte - Anzahl der Funktionsparameter* ($m - n$).

1. Sofern  $\chi^2/\text{ndof} >> 1$: sollte die Hypothese bzw. die Fitfunktion angezweifelt werden. Sie beschreibt in diesem Fall die Messdaten nur unzureichend. (Bzw. sollte $\chi^2/\text{ndof} > 1$ kann dies auch bedeuten, dass die Unsicherheiten unterschätzt sind)
2. Sofern $\chi^2/\text{ndof} \approx 1$: beschreibt die Hypothese bzw. die Fitfunktion die Daten wie erwartet und wird nicht abgelehnt. 
3. Falls $\chi^2/\text{ndof} << 1$ beschreibt die Hypothese bzw. die Fitfunktion die Daten wesentlich besser als erwartet. In diesem Fall heißt das nicht automatisch, dass unsere Hypothese falsch ist, aber man sollte überprüfen, ob die gemessenen Fehler nicht überschätzt worden sind (oder eine Korrelation zwischen den Messfehlern vorliegt).  

Sofern Sie eine Arbeit schreiben und Ihre **Goodness-of-the-Fit** ($\chi^2/\text{ndof}$) angeben wollen, so geben Sie immer beides an, das $\chi^2$ und die Anzahl an Freiheitsgraden *ndof*. Beide Werte getrennt haben einen größeren Informationsgehalt als der resultierende Quotient (Genaueres lernen Sie z.B. in der Vorlesung *Statistik, Datenanalyse und Simulationen* im Master).

Sehen wir uns hierzu nochmal unseren Doppelpeakfit etwas genauer an. `iminuit` berechnet hier für uns bereits das reduzierete $\chi^2$.

In [ ]:
mi

Eine eigene Abschätzung für das $\chi^2$ ergibt:

In [ ]:
def chi_square_ndof(x_values, y_values, dy_values, fit_model, minuit):
    ndof = len(x_values) - len(minuit.values)
    chi2 = np.sum((y_values - fit_model(x_values, *minuit.values))**2/dy_values**2)
    return chi2, ndof


chi_square, ndof = chi_square_ndof(center, entries, np.sqrt(entries), fit_model, mi)
print(chi_square, ndof, chi_square/ndof)

### Hypothesen-Test mittels $\chi^2$
Wie schon im vorherigen Abschnitt erwähnt, kann man das $\chi^2$ auch dazu verwenden, die Gültigkeit des gewählten Models zu prüfen.
Hierzu schauen wir uns die $\chi^2$-Verteilung an. Der einzige freie Parameter ist die Anzahl der Freiheitsgrade. Die Anzahl der Freiheitsgrade ist auch gleichzeitig der Erwartungswert der $\chi^2$-Verteilung. In unserem Beispiel oben ist die Anzahl der Freiheitsgrade 112 und die entsprechende Verteilung sieht wie folgt aus...

In [527]:
from scipy.stats import chi2
# chi_distribution = lambda x, ndof: chi2.pdf(x, ndof)

In [ ]:
x = np.arange(40., 180.)
# plt.plot(x, chi_distribution(x, 112))
plt.plot(x,chi2.pdf(x, 112))
x = np.arange(chi_square, 180, 0.1)
plt.fill_between(x, chi2.pdf(x, 112), alpha=0.3)
plt.ylim(0, None)
plt.xlabel('x')
plt.ylabel('$\chi^2(x)$')
plt.show()

Der erste Schritt für den Hypothesen-Test ist die Berechnung des $P$-Werts
$$ P = \int_{\chi^2}^{\infty} f(z,n_d)dz $$
wobei $f(z,n_d)$ die $\chi^2$-Verteilung und $n_d$ die Anzahl der Freiheitsgrade ist.
Im Bild oben entspricht dies der ausgefüllten Fläche.

Die praktische Berechnung erfolgt mittels der kumulativen Verteilungsfunktion via
$$ P = 1 - \chi^2_{CDF}(x, n_d) $$
wobei für $x$ das im Fit bestimmte $\chi^2$ eingesetzt wird. Die praktische Bedeutung des $P$-Werts ist die Wahrscheinlichkeit bei einer Wiederholung des Experiments in größeres $\chi^2$ zu erhalten, wenn unser Model die Daten richtig beschreibt und die ermittelten Fitparameter den wahren Werten entsprechen.

In [ ]:
p_value = lambda x, ndof: 1 - chi2.cdf(x, ndof)
p_value(chi_square, ndof), p_value(chi_square*10, ndof*10), p_value(ndof, ndof)

Kehren wir zu unserem Doppelpeak-Spektrum zurück und änderen das Fitmodell, indem wir statt eines exponentiellen einen konstanten Untergrund annehmen.

In [ ]:
def alternative_fit_model(x, A_p1, A_p2, mu_p1, mu_p2, sigma_p1, sigma_p2, c):
    return peak(x, A_p1, mu_p1, sigma_p1) + peak(x, A_p2, mu_p2, sigma_p2) + c

ls = cost.LeastSquares(center, entries, np.sqrt(entries), alternative_fit_model)

mi = Minuit(ls, 
            A_p1 = 800, 
            A_p2 = 1400,
            mu_p1 = 54,
            mu_p2 = 60,
            sigma_p1 = 2,
            sigma_p2 = 2,
            c = 100, 
           )
mi.limits['c'] = (0, None)
mi.fixed[:] = True
ls.mask = (center < 45) | (center >= 70)
mi.fixed[['c']] = False
mi.migrad()
ls.mask = None
mi.values['A_p1'] = 700
mi.values['sigma_p1'] = 3
mi.fixed[:] = True
mi.fixed[['A_p1', 'mu_p1', 'sigma_p1']] = False
mi.migrad()
mi.fixed[:] = True
mi.fixed[['A_p2', 'mu_p2', 'sigma_p2']] = False
mi.migrad()
mi.fixed[:] = False
mi.migrad()
mi.hesse()

Diese Änderung ist gering und der Fit scheint die Daten weiterhin zu beschreiben. Allerdings gibt bei kleinen Energien eine deutlich sichtbare Diskrepanz. Dies zeigt sich auch in einem größeren $\chi^2$-Wert. Wie wirkt sich dies auf den $P$-Wert aus?

In [ ]:
chi_square, ndof = chi_square_ndof(center, entries, np.sqrt(entries), alternative_fit_model, mi)
print(chi_square, ndof, chi_square/ndof)

In [ ]:
p_value = lambda x, ndof: 1 - chi2.cdf(x, ndof)
print(chi_square, ndof)
p_value(chi_square, ndof)

Der Fit ist offensichtlich viel schlechter und der $P$-Wert liegt nahe bei null, so dass man dieses Model ausschließen sollte.

Was aber, wenn die Änderung nicht so dramatisch ist? Ist ein $P$-Wert von 0,4 besser als 0,2? Nein, das kann man so nicht beantworten. Aber für einen Hypothesen-Test sollten man vorher eine Schwelle festlegen für die Akzeptanz oder Ablehnung des Models.

Wie ein solcher Hypothesen-Test aussehen kann, wollen wir im Folgenden betrachten. Hierbei benutzen wir
1. ein korrektes Model (Normalverteilung),
2. ein korrektes Model mit überschätztem Fehler (10% größer),
3. und ein falsches Model (Lorentzverteilung)

In [264]:
def lorentzian( x, x0, a, gam ):
    return a * gam**2 / ( gam**2 + ( x - x0 )**2)

Den Fit der drei Modelle und die Bestimmung des entsprechenden $P$-Werts wiederholen wir 5000-mal um eine ausreichende Statistik zu erhalten.

In [7]:
# Diese Zelle nur auf JupyterHub des ZDV ausführen um `tqdm` zu installieren falls es nicht vorhanden sein sollte!
# import sys
# import subprocess
# subprocess.check_call([
#     sys.executable, 
#     '-m',
#     'pip',
#     'install',
#     '--proxy',
#     'http://webproxy.zdv.uni-mainz.de:3128',
#     'tqdm'
# ])

In [ ]:
from tqdm.notebook import tqdm

res_good_model = []
res_overfitting = []
res_wrong_model = []

def peak(x, A, mu, sigma):
    return A*np.exp(-(x-mu)**2/(2*sigma**2))

def lorentzian( x, x0, a, gam ):
    return a * gam**2 / ( gam**2 + ( x - x0 )**2)


for i in tqdm(range(5000)):
    
    test_data = np.random.normal(0, 2, 5000)
    
    entries, edges = np.histogram(test_data, bins=25, range=(-4,4))
    center = edges[:-1] + np.diff(edges)/2
    
    ls = cost.LeastSquares(center, entries, np.sqrt(entries), peak)
    mi = Minuit(ls, 
                mu=0.1,
                sigma=1.5,
                A = 300
               )
    mi.migrad()
    
    chi, ndof = chi_square_ndof(center, entries, np.sqrt(entries), peak, mi)
    res_good_model.append(p_value(chi, ndof))


    ls = cost.LeastSquares(center, entries, np.sqrt(entries)*1.1, peak)
    mi = Minuit(ls, 
                mu=0.1,
                sigma=1.5,
                A = 300
               )
    mi.migrad()
    
    chi, ndof = chi_square_ndof(center, entries, np.sqrt(entries)*1.1, peak, mi)
    res_overfitting.append(p_value(chi, ndof))


    ls = cost.LeastSquares(center, entries, np.sqrt(entries), lorentzian)
    mi = Minuit(ls, 
                x0=0,
                gam=3,
                a = 300,
               )
    mi.migrad()
    
    chi, ndof = chi_square_ndof(center, entries, np.sqrt(entries), lorentzian, mi)
    res_wrong_model.append(p_value(chi, ndof))

res_wrong_model = np.array(res_wrong_model)
res_good_model = np.array(res_good_model)
res_overfit_model = np.array(res_overfitting)

Die Schwelle des $P$-Werts für den Hypothesen-Test setzen wir auf 0,1, d.h. Ergebnisse mit eine, $P$-Wert $<$ 0,1 werden verworfen, alle anderen akzeptiert.

In [ ]:
fig, axes = plt.subplots()
axes.hist(res_good_model, bins=25, range=(0, 1), histtype='step', color='purple', label='Good model')
axes.hist(res_wrong_model, bins=25, range=(0, 1), histtype='step', color='orange', label='Wrong model')
axes.hist(res_overfitting, bins=25, range=(0, 1), histtype='step', color='firebrick', label='Too large uncertainties (10 %)')
axes.set_xlabel('p-value')
axes.set_ylabel('Number of fits')
axes.legend()
axes.axvline(0.1, color='k')
axes2 = plt.twiny()
axes2.set_xlabel('Red. $\chi^2$')
axes2.set_xticks([0.2, 0.5, 0.8], ['> 1', '1', '< 1'])
plt.show()

axes.set_yscale('log')
fig

Wie man sieht, wird das falsche Modell nahezu immer verworfen während das richtige Modell meistens nicht verworfen wird. Das Modell mit dem überschätzten Fehler wird sogar häufiger akzeptiert, so dass man hier keine Unterscheidung vornehmen kann.

In [ ]:
print(f'Fraction of wrong model fits rejected: {np.sum(res_wrong_model<0.1)/len(res_wrong_model):.4f}')
print(f'Fraction of good model fits rejected: {np.sum(res_good_model<0.1)/len(res_good_model):.4f}')
print(f'Fraction of overfitting model fits rejected: {np.sum(res_overfit_model<0.1)/len(res_overfit_model):.4f}')

Wenn man das Limit für den Hypothesen-Test auf 0,05 festlegt, ändern die Ergebnisse wie folgt:

In [ ]:
print(f'Fraction of wrong model fits rejected: {np.sum(res_wrong_model<0.05)/len(res_wrong_model):.4f}')
print(f'Fraction of good model fits rejected: {np.sum(res_good_model<0.05)/len(res_good_model):.4f}')
print(f'Fraction of overfitting model fits rejected: {np.sum(res_overfit_model<0.05)/len(res_overfit_model):.4f}')

Der Hypothesen-Test kann das Modell nicht ablehnen, statt es zu bestätigen!